In [6]:
import numpy as np
import pandas as pd

In [ ]:
import os 

obj = np.load("/home/ne34gux/workspace/experiments/data/rotated_vessel_point_data/case_k_003_left_51deg.npz")
xyz = obj["fluid_points"]
vel = obj["sys_vel"]
xyz.shape, vel.shape

In [ ]:
import plotly.graph_objects as go

vis_indices = np.random.choice(xyz.shape[0], 1000, replace=False)

xyz_sampe = xyz[vis_indices]
vel_sampe = vel[vis_indices]

fig = go.Figure(data=[go.Cone(
    x=xyz_sampe[:,0], 
    y=xyz_sampe[:,1], 
    z=xyz_sampe[:,2],
    u=vel_sampe[:,0], 
    v=vel_sampe[:,1], 
    w=vel_sampe[:,2],
    colorscale='Viridis',
    sizemode='absolute',
    sizeref=10,  # Increase the size reference to make the cones bigger
    showscale=True
    )])
fig.update_layout(scene=dict(
            xaxis_title='X Axis',
            yaxis_title='Y Axis',
            zaxis_title='Z Axis'),
            title="Prediction",
            height=800,
            width=800)
fig.show()

In [ ]:
file_name = "/home/ne34gux/workspace/experiments/data/pinn_blood_flow_geometries/cylinder_velocities.csv"

pd.read_csv(file_name).head()

In [ ]:
data = pd.read_csv(file_name).to_numpy()
data

In [ ]:
xyz = data[:,4:7]
xyz

In [ ]:
vel = data[:,0:3]
vel

In [ ]:
vis_indices = np.random.choice(xyz.shape[0], 1000, replace=False)

xyz_sampe = xyz[vis_indices]
vel_sampe = vel[vis_indices]

xyz_sampe.shape, vel_sampe.shape

In [ ]:
import plotly.graph_objects as go

fig = go.Figure(data=[go.Cone(
    x=xyz_sampe[:,0], 
    y=xyz_sampe[:,1], 
    z=xyz_sampe[:,2],
    u=vel_sampe[:,0], 
    v=vel_sampe[:,1], 
    w=vel_sampe[:,2],
    colorscale='Viridis',
    sizemode='absolute',
    sizeref=1,  # Increase the size reference to make the cones bigger
    showscale=True
    )])
fig.update_layout(scene=dict(
            xaxis_title='X Axis',
            yaxis_title='Y Axis',
            zaxis_title='Z Axis'),
            title="Prediction",
            height=800,
            width=800)
fig.show()

In [ ]:
import torch

def normalize_point_cloud(point_cloud):
    min_vals = torch.min(point_cloud, dim=0)[0]
    max_vals = torch.max(point_cloud, dim=0)[0]
    middle_point = (min_vals + max_vals) / 2
    
    translated_point_cloud = point_cloud - middle_point
    
    scale_factor = torch.max(max_vals - min_vals)
    
    normalized_point_cloud = translated_point_cloud / scale_factor
    
    return normalized_point_cloud + 0.5

# Example usage
point_cloud = torch.tensor([[0, 0, 0], [1, 1, 1], [2, 2, 2], [3,3,3]], dtype=torch.float32)
normalized_point_cloud = normalize_point_cloud(point_cloud)
print(normalized_point_cloud)

In [2]:
import os
import numpy as np
import torch

DATA_PATH = "/home/ne34gux/workspace/experiments/data/vessel_grid64_data"
npz_files = [f for f in os.listdir(DATA_PATH) if f.endswith(".npz")]
np.load(os.path.join(DATA_PATH, npz_files[0]))["vessel_mask"].shape

(64, 64, 64)

In [3]:
xyz = np.load(os.path.join(DATA_PATH, npz_files[0]))["vessel_mask"]
vel = np.load(os.path.join(DATA_PATH, npz_files[0]))["interp_vel"]

xyz.shape, vel.shape

((64, 64, 64), (64, 64, 64, 3))

In [4]:
import torch

def reshape_vel(vel):
    d1, d2, d3, p = vel.shape
    new_shape = (d1 * d2 * d3, p)
    return torch.Tensor(vel).view(new_shape)

def create_grid_points(cube_size):
    x = torch.linspace(0, 1, cube_size)
    y = torch.linspace(0, 1, cube_size)
    z = torch.linspace(0, 1, cube_size)
    
    grid = torch.stack(torch.meshgrid(x, y, z), dim=-1)
    return grid.view(-1, 3)

def grid_to_point_cloud(mask, vel):
    cube_size = mask.shape[0]
    grid = create_grid_points(cube_size)
    point_vel = reshape_vel(vel)
    return grid, point_vel

grid_to_point_cloud(xyz, vel)

/home/ne34gux/workspace/experiments/.venv/lib64/python3.9/site-packages/torch/functional.py:513: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at ../aten/src/ATen/native/TensorShape.cpp:3609.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]


(tensor([[0.0000, 0.0000, 0.0000],
         [0.0000, 0.0000, 0.0159],
         [0.0000, 0.0000, 0.0317],
         ...,
         [1.0000, 1.0000, 0.9683],
         [1.0000, 1.0000, 0.9841],
         [1.0000, 1.0000, 1.0000]]),
 tensor([[0., 0., 0.],
         [0., 0., 0.],
         [0., 0., 0.],
         ...,
         [0., 0., 0.],
         [0., 0., 0.],
         [0., 0., 0.]]))

In [9]:
import plotly.graph_objects as go

xyz_sample, vel_sample = grid_to_point_cloud(xyz, vel)

vis_indices = np.random.choice(xyz_sample.shape[0], 50000, replace=False)

xyz_sample = xyz_sample[vis_indices]
vel_sample = vel_sample[vis_indices]


fig = go.Figure(data=[go.Cone(
    x=xyz_sample[:,0], 
    y=xyz_sample[:,1], 
    z=xyz_sample[:,2],
    u=vel_sample[:,0], 
    v=vel_sample[:,1], 
    w=vel_sample[:,2],
    colorscale='Viridis',
    sizemode='absolute',
    sizeref=1,  # Increase the size reference to make the cones bigger
    showscale=True
    )])
fig.update_layout(scene=dict(
            xaxis_title='X Axis',
            yaxis_title='Y Axis',
            zaxis_title='Z Axis'),
            title="Prediction",
            height=800,
            width=800)
fig.show()

In [33]:
import torch

batch_size = 4
num_points = 10
num_features = 3

xyz = torch.randint(low = 0, high=1000, size=(batch_size, num_points, num_features))/100
vel = torch.randn(batch_size, num_points, num_features)

xyz.shape, xyz[0], vel.shape, vel[0]

(torch.Size([4, 10, 3]),
 tensor([[2.1200, 1.8100, 6.8200],
         [8.9400, 2.4600, 2.5300],
         [7.4000, 3.6300, 6.3600],
         [6.7700, 7.2500, 7.5400],
         [2.6400, 8.7600, 6.5600],
         [1.3700, 8.2000, 3.5400],
         [3.5100, 7.6000, 1.8000],
         [2.6800, 7.4900, 1.2300],
         [2.4200, 0.0100, 5.2700],
         [2.6700, 9.8200, 0.3300]]),
 torch.Size([4, 10, 3]),
 tensor([[ 0.8153,  1.9027,  0.7808],
         [ 0.4170, -0.9443,  1.3867],
         [-1.1143,  0.5316, -1.0453],
         [ 0.0762,  1.4466,  0.1970],
         [ 1.6437,  0.9873,  1.4256],
         [-0.2232, -1.0558, -1.8480],
         [ 1.2340, -0.8480,  1.9662],
         [ 0.2465,  0.0302, -1.3049],
         [-0.7067, -1.6463, -0.1050],
         [ 2.2698, -0.5679,  0.2256]]))

In [34]:
def get_k_closest_points(tensor, k=5):
    distances = torch.cdist(tensor, tensor, p=2)  # Shape (B, N, N)
    _, indices = torch.topk(distances, k=k+1, largest=False)  # Shape (B, N, k+1)
    closest_neighbors_indices = indices[:, :, :]  # Shape (B, N, k)
    return closest_neighbors_indices

idx = get_k_closest_points(xyz, k=5)
idx.shape, idx[0]

(torch.Size([4, 10, 6]),
 tensor([[0, 8, 2, 4, 3, 5],
         [1, 2, 3, 8, 6, 0],
         [2, 3, 1, 0, 8, 4],
         [3, 2, 4, 6, 5, 0],
         [4, 5, 3, 6, 7, 9],
         [5, 7, 6, 4, 9, 3],
         [6, 7, 9, 5, 4, 3],
         [7, 6, 9, 5, 4, 3],
         [8, 0, 2, 1, 6, 5],
         [9, 7, 6, 5, 4, 3]]))

In [ ]:
# xyz.shape = torch.Size([4, 10, 3]
# idx.shape = torch.Size([4, 10, 6]

xyz[idx]
xyz.reshape(-1, 3)[idx.reshape(-1, 6)]


IndexError: index 7 is out of bounds for dimension 0 with size 4

In [39]:
xyz.reshape(-1, num_features)[idx.reshape(-1, 6)][:,0].unsqueeze(1).shape

torch.Size([40, 1, 3])

In [38]:
xyz.reshape(-1, num_features)[idx.reshape(-1, 6)][:,1:].shape

torch.Size([40, 5, 3])

In [42]:
(xyz.reshape(-1, num_features)[idx.reshape(-1, 6)][:,1:] - xyz.reshape(-1, num_features)[idx.reshape(-1, 6)][:,0].unsqueeze(1)).shape

torch.Size([40, 5, 3])

In [43]:
idx_flat = idx.reshape(-1, 6)
xyz_flat = xyz.reshape(-1, num_features)
xyz_neighbors = xyz_flat[idx_flat]

idx_flat.shape, xyz_flat.shape, xyz_neighbors.shape

(torch.Size([40, 6]), torch.Size([40, 3]), torch.Size([40, 6, 3]))

In [44]:
idx_flat

tensor([[0, 8, 2, 4, 3, 5],
        [1, 2, 3, 8, 6, 0],
        [2, 3, 1, 0, 8, 4],
        [3, 2, 4, 6, 5, 0],
        [4, 5, 3, 6, 7, 9],
        [5, 7, 6, 4, 9, 3],
        [6, 7, 9, 5, 4, 3],
        [7, 6, 9, 5, 4, 3],
        [8, 0, 2, 1, 6, 5],
        [9, 7, 6, 5, 4, 3],
        [0, 5, 3, 1, 2, 7],
        [1, 2, 5, 7, 0, 3],
        [2, 7, 1, 5, 3, 9],
        [3, 5, 8, 0, 2, 7],
        [4, 9, 7, 2, 3, 8],
        [5, 3, 0, 2, 7, 1],
        [6, 8, 3, 5, 4, 0],
        [7, 2, 9, 5, 4, 1],
        [8, 6, 3, 4, 5, 0],
        [9, 4, 7, 2, 5, 3],
        [0, 2, 9, 5, 3, 7],
        [1, 3, 5, 8, 0, 4],
        [2, 0, 9, 5, 3, 7],
        [3, 5, 1, 0, 4, 2],
        [4, 7, 3, 6, 8, 1],
        [5, 3, 1, 2, 0, 9],
        [6, 7, 8, 4, 0, 3],
        [7, 4, 6, 3, 0, 8],
        [8, 1, 6, 7, 3, 4],
        [9, 0, 2, 5, 3, 6],
        [0, 4, 5, 2, 7, 3],
        [1, 9, 6, 8, 3, 7],
        [2, 7, 0, 5, 4, 3],
        [3, 7, 8, 2, 9, 4],
        [4, 0, 5, 2, 7, 3],
        [5, 0, 4, 2,

In [4]:
import numpy as np

vessel_obj = np.load("/home/ne34gux/workspace/experiments/data/vessel_relative_data/case_k_003_left_fluid_input_target.npz")
print(vessel_obj.keys())
vessel_obj["input"].shape, vessel_obj["target"].shape

KeysView(NpzFile '/home/ne34gux/workspace/experiments/data/vessel_relative_data/case_k_003_left_fluid_input_target.npz' with keys: input, target, reference)


((104492, 8), (104492, 3))